# GNA : MOSI UseCase

This notebooks provides a testing bed and configuration utility for <strong>GNA - MOSI</strong> use case served by <em>gCube CMS Suite</em>, by:

- Creating UCD from schema URL
- Registering MOSI UCD in corrent gCube Context
- Parsing and registration of MOSI records from CSV (if provided)
- Publication of registered MOSI records
- Deletion of registered MOSI records

NB This notebook relies on <strong>commons.ipynb</strong> distributed along with <em>gCube CMS Suite</em>

## Parameters Initialization

In [32]:
%run commons.ipynb
# These parameters should be discovered / initialized by common gcube libraries. 
gcube_token = "3aa85bbf-d5f3-4df4-ad03-4f8f788eba3d-98187548"
service_base_endpoint ="https://geoportal.dev.int.d4science.net/geoportal-service/srv"

# Actual customizable parameters
ucid = "GNA-MOSI"
gpkgFile = "templateItalia.gpkg"
verbose=False

#NB The following should not be changed 
projects_endpoint = service_base_endpoint + "/projects/"+ucid
ucds_endpoint = service_base_endpoint + "/ucd/"
ucd_endpoint = ucds_endpoint+ucid
plugins_endpoint=service_base_endpoint + "/plugins/"

In [4]:
# Init parameters
UCD = {
  "_id" : ucid,
  "_mongoId":None,
  "_version" : "1.0.0",
  "_name" : "GNA : MOSI",
  "_description" : "Modulistica siti",
  "_handlers" : []
}

## UCD Definition and Registration

In [25]:
#Check if already existing
send(method="GET",dest=ucd_endpoint)

{'_mongoId': '626a972102ad3d3b47050dfd',
 '_id': 'GNA-MOSI',
 '_version': '1.0.0',
 '_name': 'GNA : MOSI',
 '_description': 'Modulistica siti',
 '_creationInfo': None,
 '_schema': None,
 '_handlers': [{'_id': 'DEFAULT-SINGLE-STEP',
   '_type': 'LifecycleManagement',
   '_configuration': {'step_access': [{'STEP': 'PUBLISH', 'roles': []}]}},
  {'_id': 'SDI-Indexer-Plugin',
   '_type': 'Indexer',
   '_configuration': {'explicitFieldMapping': [],
    'additionalLayers': [{'source': {'url': '...'}, 'toSetTitle': ''}]}}],
 '_dataAccessPolicies': [{'_policy': {'_write': 'own', '_read': 'any'},
   '_roles': [],
   '_enforcer': None}]}

In [ ]:
# should read schema from git repo
schema_url="https://code-repo.d4science.org/gCubeSystem/gcube-cms-suite/raw/branch/%2322686/test-data/profiledDocuments/schemas/MOSI-schema.json"
schema=send(method="GET",dest=schema_url)
#NB Cannot set schema from gpkg.MOSI if we want it structured
#with fiona.open(gpkgFile, layer='MOSI_multipolygon') as layer:
#    feature = layer[0]
    #feature is GeoJSON
UCD.update({"_schema" :schema})

In [6]:
#TODO DEFINE ROLES
UCD.update({"_dataAccessPolicies" : [
    {"_policy" : {"_read" : "any", "_write" : "own"}, "_roles":[]},
  ]})

In [7]:
# UPDATE Lifecycle Settings
UCD["_handlers"].append({
      "_id" :  "DEFAULT-SINGLE-STEP",
      "_type" :  "LifecycleManagement",
      "_configuration" : {
        "step_access" : [
          {"STEP" : "PUBLISH", "roles" :[]}
        ]
      }
    })

In [9]:
# UPDATE Lifecycle Settings
UCD["_handlers"].append({
      "_id" : "SDI-Indexer-Plugin",
      "_type" : "Indexer",
      "_configuration" : {
# TODO use 
#     "bboxEvaluation" : ["$..posizionamentoScavo.._bbox"],
        "explicitFieldMapping" : [
#TODO READ FROM MOSI LAYER 
        ],
        "additionalLayers" : [
# TODO CONFIGURE Additional
          {"source" : {"url" :  "..."},"toSetTitle":""}
        ]
      }
    }
    )

In [11]:
# Update in context

#UCD.update({"_id":"1234","_schema":{}})
print_json(data=UCD)


send(method="POST",data=json.dumps(UCD),dest=ucds_endpoint)

{
  "_id": "GNA-MOSI",
  "_mongoId": null,
  "_version": "1.0.0",
  "_name": "GNA : MOSI",
  "_description": "Modulistica siti",
  "_handlers": [
    {
      "_id": "DEFAULT-SINGLE-STEP",
      "_type": "LifecycleManagement",
      "_configuration": {
        "step_access": [
          {
            "STEP": "PUBLISH",
            "roles": []
          }
        ]
      }
    },
    {
      "_id": "SDI-Indexer-Plugin",
      "_type": "Indexer",
      "_configuration": {
        "explicitFieldMapping": [],
        "additionalLayers": [
          {
            "source": {
              "url": "..."
            },
            "toSetTitle": ""
          }
        ]
      }
    }
  ],
  "_dataAccessPolicies": [
    {
      "_policy": {
        "_read": "any",
        "_write": "own"
      },
      "_roles": []
    }
  ]
}

GOING TO SEND POST REQUEST TO https://geoportal.dev.int.d4science.net/geoportal-service/srv/ucd/
Data is {'_id': 'GNA-MOSI', '_mongoId': None, '_version': '1.0.0', '_name': 'GNA : MOSI', '_description': 'Modulistica siti', '_handlers': [{'_id': 'DEFAULT-SINGLE-STEP', '_type': 'LifecycleManagement', '_configuration': {'step_access': [{'STEP': 'PUBLISH', 'roles': []}]}}, {'_id': 'SDI-Indexer-Plugin', '_type': 'Indexer', '_configuration': {'explicitFieldMapping': [], 'additionalLayers': [{'source': {'url': '...'}, 'toSetTitle': ''}]}}], '_dataAccessPolicies': [{'_policy': {'_read': 'any', '_write': 'own'}, '_roles': []}]}
RESPONSE STATUS 500
CAUSE 
<!doctype html><html lang="en"><head><title>HTTP Status 500 ? Internal Server Error</title><style type="text/css">h1 {font-family:Tahoma,Arial,sans-serif;color:white;background-color:#525D76;font-size:22px;} h2 {font-family:Tahoma,Arial,sans-serif;color:white;background-color:#525D76;font-size:16px;} h3 {font-family:Tahoma,Arial,sans-serif;colo

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

# MOSI Records parsing and registration

In [2]:
# GPKG support
# import fiona


In [19]:
!pip install pandas
import pandas as pd
import numpy as np

In [23]:
# creating a data frame
df = pd.read_csv("MOSI_multipolygon_templateIta.csv",delimiter = ",")    
for row in df.itertuples():
        mosi={
      "CD" : {
        "TSK" : row.TSK,
          #SIGEC Web fields... ask Mibac
#        "CMD" : row.CMD,
#        "ESC" : row.ESC,
#        "ECP" : row.ECP,
        "CBC" : row.CBC,
        "ACC" : {
          "ACCE" : row.ACCE,
          "ACCC" : row.ACCC,
          "ACCS" : row.ACCS
        }
      },
      "OG" : {
        "AMB" : row.AMB,
        "AMA" : row.AMA,
        "OGD": row.OGD,
        "OGT" : row.OGT,
        "OGN" : row.OGN
      },
      "LC" : {
        "LCS" : row.LCS,
        "LCR" : row.LCR,
        "LCP" : row.LCP,
        "LCC" : row.LCC,
        "LCI" : row.LCI,
        "PVL" : row.PVL,
        "PVZ" : row.PVZ,
        "ACB" : {
          "ACBA" : row.ACBA,
          "ACBS" : row.ACBS
        }
      },
      "DT" : {
        "DTR" : row.DTR,
        "DTT" : row.DTT
      },
      "DA" : {
        "DES" : row.DES,
        "OGM": row.OGM
      },
      "GE" : {
        "GEL" : row.GEL,
        "GET" : row.GET,
        "GEP" : row.GEP,
        "GEC" : {
          "GECX" : row.GECX,
          "GECY" : row.GECY
        },
        "GPT": row.GPT,
        "GPM": row.GPM,
        "GPB" : {
          "GPBB" : row.GPBB
        }
      },
      "TU" : {
        "CDG": {
          "CDGG": row.CDGG
        },
        "BPT" : row.BPT,
        "NVC": {
          "NVCT" : row.NVCT,
          "NVCM" : row.NVCM,
          "NVCE" : row.NVCE,
          "NVCP" : row.NVCP,
            
            # Not found in csv
#          "NWCN" : row.NWCN
        },
        "STU":{
          "STUE" : row.STUE,
          "STUT" : row.STUT,
          "STUS" : row.STUS
        }
      },
      "RE" : {
        "RCG": {
          "RCGV" : row.RCGV,
          "RCGD" : row.RCGD,
          "RCGT" : row.RCGT,
          "RCGE" : row.RCGE
        },
        "MTP" : {
          "MTPC": row.MTPC,
          "MTPZ" : row.MTPZ
        },
        "MTZ" : row.MTZ,
        "FOI" : {
          "FOIT" : row.FOIT,
          "FOIR" : row.FOIR,
          "FOIA" : row.FOIA,
          "FOIQ" : row.FOIQ,
          "FOIF" : row.FOIF,
          "FOIO" : row.FOIO,
          "FOIN" : row.FOIN
        }
      },
      "IP" : {
        "IAP" : {
          "IAPN" : row.IAPN,
          "IAPR" : row.IAPR,
          "IAPI" : row.IAPI,
          "IAPS" : row.IAPS
        }
      },
      "MT" : {
        "MIS" : {
          "MISZ" : row.MISZ,
          "MISU" : row.MISU,
          "MISM" : row.MISM
        },
        "MTA" : {
          "MTAP" : row.MTAP,
          "MTAM" : row.MTAM,
          "MTAX" : row.MTAX,
          "MTAR" : row.MTAR,
          "MTAS" : row.MTAS
        }
      },
      "VR" : {
        "VRP" : {
          "VRPI" : row.VRPI,
          "VRPA" : row.VRPA,
          "VRPV" : row.VRPV,
          "VRPS" : row.VRPS,
          "VRPN" : row.VRPN
        },
        "VRR" : {
          "VRRP" : row.VRRP,
          "VRRO" : row.VRRO,
          "VRRR" : row.VRRR,
          "VRRS" : row.VRRS,
          "VRRN" : row.VRRN
        }
      },
      "DO" : {
        "FTA" : {
          "FTAN" : row.FTAN,
          "FTAX" : row.FTAX,
          "FTAP" : row.FTAP,
          "FTAC" : row.FTAC
        },
        "DRA" : {
          "DRAN" : row.DRAN,
          "DRAX" : row.DRAX,
          "DRAT" : row.DRAT,
          "DRAC" : row.DRAC,
          "DRAK" : row.DRAK
        },
        "FNT" : {
          "FNTI" : row.FNTI,
          "FNTX" : row.FNTX,
          "FNTP" : row.FNTP,
          "FNTS" : row.FNTS,
          "FNTK" : row.FNTK
        },
        "BIB" : {
          "BIBR" : row.BIBR,
          "BIBX" : row.BIBX,
          "BIBM" : row.BIBM,
          "BIBN" : row.BIBN
        }
      },
      "CM" : {
        "FUR" : row.FUR,
        "CMR" : row.CMR,
        "CMC" : row.CMC,
        "CMA" : row.CMA,
        "ADP" : row.ADP
      }
    }
        mosi = send(method="POST",data=json.dumps(mosi,ignore_nan=True),dest=projects_endpoint)
        print("Registered "+mosi["_id"])


Index(['fid', 'TSK', 'CBC', 'ACCE', 'ACCC', 'ACCS', 'AMB', 'AMA', 'OGD', 'OGT',
       ...
       'FUR', 'CMR', 'CMC', 'CMA', 'ADP', 'NOTE_INT', 'BIBM', 'DOZ', 'GECS',
       'APED'],
      dtype='object', length=106)
GOING TO SEND POST REQUEST TO https://geoportal.dev.int.d4science.net/geoportal-service/srv/projects/GNA-MOSI
Data is {"CD": {"TSK": "MOSI", "CBC": null, "ACC": {"ACCE": null, "ACCC": "SABAP-TO_2019_107_0006_a_b", "ACCS": null}}, "OG": {"AMB": "archeologico", "AMA": "archeologia preventiva", "OGD": "sito pluristratificato", "OGT": "{}", "OGN": "a) Belmonte (Valperga-Pertusio-Prascorsano),\nVersante N (B1), alto versante SE (BE2), sommit\u00e0 Campass (BE3, BE6), alto versan- te S (BE4), riparo da stacco graniti (?, BE5), estremit\u00e0 W del colle (BE7); b-c)  Belmonte (Valperga-Pertusio-Prascorsano)"}, "LC": {"LCS": "Italia", "LCR": "Piemonte", "LCP": "TO", "LCC": "Valperga", "LCI": null, "PVL": "Belmonte (Valperga-Pertusio-Prascorsano)\n", "PVZ": null, "ACB": {"ACBA": n

## MOSI Record publication

Set <strong>PUBLISHING = True</strong> below to activate this section.

In [37]:
PUBLISH=True

In [48]:
#Get all existing MOSI
existing=send(method="GET",dest=projects_endpoint)

In [51]:
for r in existing :
    print(r['_id']+" "+r['_theDocument']['OG']['OGN'])

626a99c502ad3d3b47050e00 a) Belmonte (Valperga-Pertusio-Prascorsano),
Versante N (B1), alto versante SE (BE2), sommità Campass (BE3, BE6), alto versan- te S (BE4), riparo da stacco graniti (?, BE5), estremità W del colle (BE7); b-c)  Belmonte (Valperga-Pertusio-Prascorsano)
626a99c602ad3d3b47050e01 via Peradotto, F. VIII cat. di Valperga
626a99c702ad3d3b47050e02 Tempagnano - Valdottavo
626a99c702ad3d3b47050e03 Frizzone
626a99c702ad3d3b47050e04 Castelvecchio - Villa Ravano
626a99c802ad3d3b47050e05 Pozzuolo


In [58]:
verbose = False 
if PUBLISH : 
    STEPrequest={"stepID" : "PUBLISH"}
    for r in existing:
        send(method="POST",data=json.dumps(STEPrequest),dest=projects_endpoint+"/step/"+r['_id'])

Data is {"stepID": "PUBLISH"}
Data is {"stepID": "PUBLISH"}
Data is {"stepID": "PUBLISH"}
Data is {"stepID": "PUBLISH"}
Data is {"stepID": "PUBLISH"}
Data is {"stepID": "PUBLISH"}


In [65]:
for r in send(method="GET",dest=projects_endpoint) : 
    info = r['_lifecycleInformation']
    if info['_lastOperationStatus'] != "OK" :
        print(r['_id']+" "+json.dumps(info))
    else : print(r['_id']+" "+info['_lastOperationStatus'])

626a99c502ad3d3b47050e00 {"_phase": "DRAFT", "_lastInvokedStep": "PUBLISH", "_lastOperationStatus": "ERROR", "_errorMessages": ["No Configuration found for SDI-Default-Materializer in GNA-MOSI"], "_warningMessages": [], "_triggeredEvents": [], "_notes": null}
626a99c602ad3d3b47050e01 {"_phase": "DRAFT", "_lastInvokedStep": "PUBLISH", "_lastOperationStatus": "ERROR", "_errorMessages": ["No Configuration found for SDI-Default-Materializer in GNA-MOSI"], "_warningMessages": [], "_triggeredEvents": [], "_notes": null}
626a99c702ad3d3b47050e02 {"_phase": "DRAFT", "_lastInvokedStep": "PUBLISH", "_lastOperationStatus": "ERROR", "_errorMessages": ["No Configuration found for SDI-Default-Materializer in GNA-MOSI"], "_warningMessages": [], "_triggeredEvents": [], "_notes": null}
626a99c702ad3d3b47050e03 {"_phase": "DRAFT", "_lastInvokedStep": "PUBLISH", "_lastOperationStatus": "ERROR", "_errorMessages": ["No Configuration found for SDI-Default-Materializer in GNA-MOSI"], "_warningMessages": [], 